thhis is finetunign  paramter search 1 with 5 data 

In [1]:
import os
import pandas as pd
import numpy as np
import torch
import re
from sklearn.metrics import accuracy_score, precision_recall_fscore_support
from torch.utils.data import Dataset, DataLoader
from transformers import AutoTokenizer, Trainer, TrainingArguments,EsmForSequenceClassification, AdamW,EsmTokenizer
from ray import tune
from ray.tune.schedulers import ASHAScheduler
from ray.tune import CLIReporter

In [2]:
import random
import numpy as np
import torch

random.seed(0)
np.random.seed(0)
torch.manual_seed(0)
torch.cuda.manual_seed_all(0)

In [3]:
print("cuda is on \nGod SpeeD 🏎️🏎️🏎️🏎️" if torch.cuda.is_available() else "cpu")

cuda is on 
God SpeeD 🏎️🏎️🏎️🏎️


In [4]:
train_data = pd.read_csv("/home/ubuntu/work/data/new/mini/balanced/train_data5.csv")
test_data = pd.read_csv("/home/ubuntu/work/data/new/mini/balanced/test_data.csv")

In [5]:
test_data["len"].max()

20

In [6]:

model = EsmForSequenceClassification.from_pretrained("facebook/esm2_t6_8M_UR50D")

Some weights of EsmForSequenceClassification were not initialized from the model checkpoint at facebook/esm2_t6_8M_UR50D and are newly initialized: ['classifier.dense.bias', 'classifier.dense.weight', 'classifier.out_proj.bias', 'classifier.out_proj.weight']
You should probably TRAIN this model on a down-stream task to be able to use it for predictions and inference.


In [7]:
class processor(Dataset):
    def __init__(self, df, tokenizer_name="facebook/esm2_t6_8M_UR50D", max_len=24):
        self.tokenizer = EsmTokenizer.from_pretrained(tokenizer_name, do_lower_case=False)
        self.max_len = max_len
        self.seqs, self.labels = self.get_seqs_labels(df)

    def get_seqs_labels(self, df):
        seqs = list(df['seq'])
        labels = list(df['type'].astype(int))
        return seqs, labels

    def __len__(self):
        return len(self.labels)

    def __getitem__(self, idx):
        seq = " ".join("".join(self.seqs[idx].split()))
        seq_ids = self.tokenizer(seq, truncation=True, padding='max_length', max_length=self.max_len)
        sample = {key: torch.tensor(val) for key, val in seq_ids.items()}
        sample['labels'] = torch.tensor(self.labels[idx])
        return sample

In [8]:
from sklearn.metrics import accuracy_score, precision_recall_fscore_support, roc_auc_score, confusion_matrix

def compute_metrics(pred):
    labels = pred.label_ids
    preds = pred.predictions.argmax(-1)  # Predicted classes
    probs = pred.predictions[:, 1]       # Probabilities for positive class

    # Calculate basic metrics
    precision, recall, f1, _ = precision_recall_fscore_support(labels, preds, average='binary')
    acc = accuracy_score(labels, preds)
    
    # Calculate confusion matrix for specificity
    tn, fp, fn, tp = confusion_matrix(labels, preds).ravel()
    specificity = tn / (tn + fp)
    
    # Calculate AUC-ROC score
    auc = roc_auc_score(labels, probs)

    return {
        'accuracy': acc,
        'f1': f1,
        'precision': precision,
        'recall': recall,
        'specificity': specificity,
        'auc_roc': auc
    }

In [9]:
def model_init():
    return  EsmForSequenceClassification.from_pretrained("facebook/esm2_t6_8M_UR50D")

In [10]:
trainingdata  = processor(train_data)
evaldata = processor(test_data)

In [11]:
search_space = {
    "num_train_epochs": tune.choice([5, 10, 15]),
    "learning_rate": tune.loguniform(1e-5, 5e-5),
    "batch_size": tune.choice([4, 8, 16]),
    "warmup_steps": tune.choice([0, 100, 500]),
    "weight_decay": tune.uniform(0.0, 0.3),
    "grad_acc_steps": tune.choice([1, 4, 8]),
    
}

# Configure Ray Tune scheduler and reporter
scheduler = ASHAScheduler(
    metric="eval_loss",
    mode="min",
    max_t=15,
    grace_period=1,
    reduction_factor=2
)

In [12]:
def trainer_tune(config):
    training_args = TrainingArguments(
        output_dir='./results',
        num_train_epochs=config["num_train_epochs"],
        learning_rate=config["learning_rate"],
        per_device_train_batch_size=config["batch_size"],
        warmup_steps=config["warmup_steps"],
        weight_decay=config["weight_decay"],
        logging_dir='./logs',
        logging_steps=100,
        evaluation_strategy="epoch",
        gradient_accumulation_steps=config["grad_acc_steps"],
        fp16=True,
        
    )

    trainer = Trainer(
        model_init=model_init,
        args=training_args,
        train_dataset=trainingdata,
        eval_dataset=evaldata,
        compute_metrics=compute_metrics,
    )

    # Train and evaluate
    trainer.train()
    eval_metrics = trainer.evaluate()

    # Return metrics to Ray Tune
    return eval_metrics

# Hyperparameter search setup
tune_analysis = tune.run(
    trainer_tune,
    config=search_space,
    resources_per_trial={"cpu": 2, "gpu": 1 if torch.cuda.is_available() else 0},
    num_samples=100,
    scheduler=scheduler,
    
    name="hyperparam-tuning"
)



2025-01-21 14:58:42,557	INFO worker.py:1771 -- Started a local Ray instance.
2025-01-21 14:58:48,031	INFO tune.py:253 -- Initializing Ray automatically. For cluster usage or custom Ray initialization, call `ray.init(...)` before `tune.run(...)`.
2025-01-21 14:58:48,032	INFO tune.py:616 -- [output] This uses the legacy output and progress reporter, as Jupyter notebooks are not supported by the new engine, yet. For more information, please see https://github.com/ray-project/ray/issues/36949


(trainer_tune pid=4168275) /home/ubuntu/anaconda3/envs/sathdeep/lib/python3.12/site-packages/transformers/training_args.py:1474: FutureWarning: `evaluation_strategy` is deprecated and will be removed in version 4.46 of 🤗 Transformers. Use `eval_strategy` instead
(trainer_tune pid=4168275)   warnings.warn(
(trainer_tune pid=4168275) Some weights of EsmForSequenceClassification were not initialized from the model checkpoint at facebook/esm2_t6_8M_UR50D and are newly initialized: ['classifier.dense.bias', 'classifier.dense.weight', 'classifier.out_proj.bias', 'classifier.out_proj.weight']
(trainer_tune pid=4168275) You should probably TRAIN this model on a down-stream task to be able to use it for predictions and inference.
(trainer_tune pid=4168275) Some weights of EsmForSequenceClassification were not initialized from the model checkpoint at facebook/esm2_t6_8M_UR50D and are newly initialized: ['classifier.dense.bias', 'classifier.dense.weight', 'classifier.out_proj.bias', 'classifier.o

(trainer_tune pid=4168275) {'eval_loss': 0.6952229738235474, 'eval_accuracy': 0.4583333333333333, 'eval_f1': 0.6198830409356725, 'eval_precision': 0.4774774774774775, 'eval_recall': 0.8833333333333333, 'eval_specificity': 0.03333333333333333, 'eval_auc_roc': 0.3794444444444445, 'eval_runtime': 0.117, 'eval_samples_per_second': 1025.264, 'eval_steps_per_second': 128.158, 'epoch': 0.93}


 42%|████▏     | 21/50 [00:03<00:04,  7.24it/s]
(trainer_tune pid=4168275) 
  0%|          | 0/15 [00:00<?, ?it/s]
(trainer_tune pid=4168275) 
                                               ]
100%|██████████| 15/15 [00:00<00:00, 131.63it/s]
                                                


(trainer_tune pid=4168275) {'eval_loss': 0.6932820677757263, 'eval_accuracy': 0.48333333333333334, 'eval_f1': 0.6436781609195402, 'eval_precision': 0.49122807017543857, 'eval_recall': 0.9333333333333333, 'eval_specificity': 0.03333333333333333, 'eval_auc_roc': 0.44430555555555556, 'eval_runtime': 0.1251, 'eval_samples_per_second': 959.314, 'eval_steps_per_second': 119.914, 'epoch': 1.95}


...

 86%|████████▌ | 43/50 [00:03<00:00, 12.53it/s]
                                               
100%|██████████| 15/15 [00:00<00:00, 282.94it/s]
                                                


(trainer_tune pid=7807) {'eval_loss': 0.6689534783363342, 'eval_accuracy': 0.65, 'eval_f1': 0.7407407407407407, 'eval_precision': 0.5882352941176471, 'eval_recall': 1.0, 'eval_specificity': 0.3, 'eval_auc_roc': 0.8041666666666667, 'eval_runtime': 0.0565, 'eval_samples_per_second': 2124.998, 'eval_steps_per_second': 265.625, 'epoch': 4.0}


 98%|█████████▊| 49/50 [00:04<00:00, 11.99it/s]
(trainer_tune pid=7807) 
                                               
100%|██████████| 50/50 [00:04<00:00, 11.99it/s] 


(trainer_tune pid=7807) {'eval_loss': 0.667431652545929, 'eval_accuracy': 0.65, 'eval_f1': 0.7407407407407407, 'eval_precision': 0.5882352941176471, 'eval_recall': 1.0, 'eval_specificity': 0.3, 'eval_auc_roc': 0.8045833333333333, 'eval_runtime': 0.0568, 'eval_samples_per_second': 2113.15, 'eval_steps_per_second': 264.144, 'epoch': 4.65}
(trainer_tune pid=7807) {'train_runtime': 4.7016, 'train_samples_per_second': 363.708, 'train_steps_per_second': 10.635, 'train_loss': 0.6793243408203125, 'epoch': 4.65}


  0%|          | 0/15 [00:00<?, ?it/s]
2025-01-21 15:30:24,665	INFO tune.py:1009 -- Wrote the latest version of all result files and experiment state to '/home/ubuntu/ray_results/hyperparam-tuning' in 0.0386s.
100%|██████████| 15/15 [00:00<00:00, 248.23it/s]
2025-01-21 15:30:24,676	INFO tune.py:1041 -- Total run time: 1896.64 seconds (1896.58 seconds for the tuning loop).


In [13]:
best_trial = tune_analysis.get_best_trial("eval_loss", "min", "last")
print("Best trial config: ", best_trial.config)
print("Best trial final metrics:")
for metric, value in best_trial.last_result.items():
    print(f"{metric}: {value}")

Best trial config:  {'num_train_epochs': 15, 'learning_rate': 2.6823346995822657e-05, 'batch_size': 8, 'warmup_steps': 100, 'weight_decay': 0.02978410510769216, 'grad_acc_steps': 4}
Best trial final metrics:
eval_loss: 0.40861865878105164
eval_accuracy: 0.825
eval_f1: 0.8235294117647058
eval_precision: 0.8305084745762712
eval_recall: 0.8166666666666667
eval_specificity: 0.8333333333333334
eval_auc_roc: 0.9043055555555556
eval_runtime: 0.1305
eval_samples_per_second: 919.457
eval_steps_per_second: 114.932
epoch: 13.953488372093023
timestamp: 1737451885
checkpoint_dir_name: None
done: True
training_iteration: 1
trial_id: 1e253_00007
date: 2025-01-21_15-01-25
time_this_iter_s: 16.26460075378418
time_total_s: 16.26460075378418
pid: 4170889
hostname: sath-prat
node_ip: 172.17.104.22
config: {'num_train_epochs': 15, 'learning_rate': 2.6823346995822657e-05, 'batch_size': 8, 'warmup_steps': 100, 'weight_decay': 0.02978410510769216, 'grad_acc_steps': 4}
time_since_restore: 16.26460075378418
ite

(raylet) [2025-01-23 04:13:24,285 E 4166298 4166328] (raylet) file_system_monitor.cc:111: /tmp/ray/session_2025-01-21_14-58-40_649325_4165946 is over 95% full, available space: 5274578944; capacity: 105492713472. Object creation will fail if spilling is required.
(raylet) [2025-01-23 04:13:34,288 E 4166298 4166328] (raylet) file_system_monitor.cc:111: /tmp/ray/session_2025-01-21_14-58-40_649325_4165946 is over 95% full, available space: 5274251264; capacity: 105492713472. Object creation will fail if spilling is required.
(raylet) [2025-01-23 04:13:44,290 E 4166298 4166328] (raylet) file_system_monitor.cc:111: /tmp/ray/session_2025-01-21_14-58-40_649325_4165946 is over 95% full, available space: 5273985024; capacity: 105492713472. Object creation will fail if spilling is required.
(raylet) [2025-01-23 04:13:54,293 E 4166298 4166328] (raylet) file_system_monitor.cc:111: /tmp/ray/session_2025-01-21_14-58-40_649325_4165946 is over 95% full, available space: 5273731072; capacity: 105492713